# Build a Kriging surrogate on some dummy prop data

**The idea here is to look at the following:**

- How do we build a Kriging model on low-fidelity data, which may not be high quailty everywhere, so we need to handle some noise?
- How do we take the low-fidelity data and supplement it with a sample of high qauilty, high-fidelity data?

In [93]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import dummy_prop_example
from smt.sampling_methods import FullFactorial, LHS
from smt.surrogate_models import KRG, KPLS, KPLSK
from smt.applications import MFK
import sys
from pathlib import Path
sys.path[0] = str(Path(sys.path[0]).parent)
# from unipy import surrogate_model

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


**The propeller we are considering here has the following properties:**

- fixed blade pitch
- A radius of 1.6 m
- Operating propeller speeds between 300 RPM and 1300 RPM
- Number of blades is irrelevant

**First let us consider a low-fidelity dataset. We could build a full factorial of data if this is cheap, so lets pretend to do that.**

We also may choose to remove some cases, since we can't always successfully manage to build a full factorial set of structured data. A key point to keep in mind it is not necessary to have structured data, unstructured is also fine.

Let us set up the sampling limits:

*Note:* that we use the kwarg `clip=True` in order for the number of points to give a full grid.

In [94]:
# setup each limit
discangle_limits = [-90.0, 90.0]
propspeed_limits = [300.0, 1300.0]
airspeed_limits = [0.0, 60.0]
# and we group them into a list
xlimits = np.array([discangle_limits, airspeed_limits, propspeed_limits])
# and make the full factorial sampling
lf_sampling = FullFactorial(xlimits=xlimits, clip=True)
number_of_lf_samples = 620
lf_independent = lf_sampling(number_of_lf_samples)
print(f"Actual number of samples generated is: {lf_independent[:, 0].shape[0]}")

Actual number of samples generated is: 648


Here is the plot of the data we just generated:

In [95]:
fig = go.Figure(
    data=[
        go.Scatter3d(
            x=lf_independent[:, 0],
            y=lf_independent[:, 1],
            z=lf_independent[:, 2],
            mode="markers",
            marker=dict(color="black", size=4),
        )
    ]
)

fig.update_layout(
    scene=dict(
        xaxis_title="disc angle [deg]",
        yaxis_title="airspeed [m/s]",
        zaxis_title="prop speed [RPM]",
    ),
)

fig.show()


**It is now time to build a Pandas DataFrame, containg all of this data**

We don't really need to do this to build a Kirging surrogate, however we are doing this as it is common that the data won't just come out as a tidy NumPy array, and instead will load the data from some .csv file or similar.

*Note:* that the arguments after the sampling points are used to caluclate the dependent variable and are unique to the propeller example we are running. It just gives some load at some propeller speed. Here we can think of it as 3000 N of thrust at 1000 RPM.

In [96]:
lf_data_df: pd.DataFrame = dummy_prop_example.lf_data(
    lf_independent[:, 0],
    lf_independent[:, 1],
    lf_independent[:, 2],
    1000.0, # prop speed in RPM
    3000.0, # the thurst at the above prop speed
)

display(lf_data_df)

airspeed  discangle    propspeed          load
0         0.0      -90.0   300.000000    270.000000
1         0.0      -90.0   442.857143    588.367347
2         0.0      -90.0   585.714286   1029.183673
3         0.0      -90.0   728.571429   1592.448980
4         0.0      -90.0   871.428571   2278.163265
..        ...        ...          ...           ...
643      60.0       90.0   728.571429  11732.448980
644      60.0       90.0   871.428571  12418.163265
645      60.0       90.0  1014.285714  13226.326531
646      60.0       90.0  1157.142857  14156.938776
647      60.0       90.0  1300.000000  15210.000000

[648 rows x 4 columns]

**At this stage, it is probably worthwhile to see what the data looks like**

*Note:* that this data and the trends are made up.

In [97]:
rpms = np.unique(lf_data_df.propspeed.to_numpy())
rpm = rpms[0]
plot_trend_df = lf_data_df[lf_data_df.propspeed == rpm]

fig = go.Figure(
    data=[
        go.Scatter3d(
            x=plot_trend_df.discangle,
            y=plot_trend_df.airspeed,
            z=plot_trend_df.load,
            mode="markers",
            marker=dict(
                color="black", size=4),
        )
    ]
)

fig.update_layout(
    scene=dict(
        xaxis_title="disc angle [deg]",
        yaxis_title="airspeed [m/s]",
        zaxis_title="thrust [N]",
    ),
    title=f"Prop speed is {rpm} RPM",
)


**Now we can build the Kirging surrogate model, from the DataFrame**

First, here is a funciton that can help us with the link between DataFrames and Numpy arrays

In [98]:
def prep_data(
    df: pd.DataFrame, headers: list[str]
) -> np.ndarray:
    """ Prepare the data for surrogate model
    Prepares an np.ndarray[nt, nx] for the Kriger, where nx is in
    the order of the specified headers
    """
    return np.asarray([df[h].to_numpy() for h in headers]).T

Now the Kriging model is made:

In [99]:
# we have yet to explore theta0, using default from docs
lf_krg_sm = KRG(theta0=[1e-2])
lf_x_data = prep_data(lf_data_df, ["discangle", "airspeed", "propspeed"])
lf_y_data = prep_data(lf_data_df, ["load"])
lf_krg_sm.set_training_values(lf_x_data, lf_y_data)

We are now ready to train the model:

In [100]:
lf_krg_sm.train()

___________________________________________________________________________
   
                                  Kriging
___________________________________________________________________________
   
 Problem size
   
      # training points.        : 648
   
___________________________________________________________________________
   
 Training
   
   Training ...
   Training - done. Time (sec): 26.3564651


**Now lets make some points for interpolation**

We will also include the training conditions, however we will just interpolate at a single propeller speed so that we can easily plot it in 3D

In [101]:
plot_rpm = rpms[0]
print(f"Interpolating at prop speed = {plot_rpm} RPM")

Interpolating at prop speed = 300.0 RPM


In [102]:
# I like to use non-equal dimensions, it helps to make sure plotting is correct!
n_discangle_lin = 50
n_airspeed_lin = 51
single_rpm = lf_data_df[lf_data_df.propspeed == propspeed_limits[0]]
# we use `*_vec_i` to hint that it's a 1D vector or interp points
discangle_vec_i = np.sort(
    np.concatenate(
        [np.linspace(-90, 90, n_discangle_lin), single_rpm.discangle.to_numpy()]
    )
)
airspeed_vec_i = np.sort(
    np.concatenate([np.linspace(0, 60, n_airspeed_lin), single_rpm.airspeed.to_numpy()])
)

# now the actual number of points
n_discangle = len(discangle_vec_i)
n_airspeed = len(airspeed_vec_i)

propspeed_vec_i = np.asarray(plot_rpm)
# and now we mesh grid, so that we can make a surface
# note that we use `*_mat_i` to show that it's not longer a vector
[discangle_mat_i, airspeed_mat_i, propspeed_mat_i] = np.meshgrid(
    discangle_vec_i, airspeed_vec_i, propspeed_vec_i
)

# data to interpolate
x_data_interp = np.asarray(
    [
        discangle_mat_i.flatten(),
        airspeed_mat_i.flatten(),
        propspeed_mat_i.flatten(),
    ]
).T
print(f"Shape of the data to interpolate is {x_data_interp.shape}")

y_data_interp = lf_krg_sm.predict_values(x_data_interp)
y_data_s2 = lf_krg_sm.predict_variances(x_data_interp)


Shape of the data to interpolate is (17292, 3)
___________________________________________________________________________
   
 Evaluation
   
      # eval points. : 17292
   
   Predicting ...
   Predicting - done. Time (sec):  3.0179725
   
   Prediction time/pt. (sec) :  0.0001745
   


We now need to reshape the data, so we can plot a surface

In [103]:
y_data_interp_plt = y_data_interp.reshape(n_airspeed, n_discangle)
y_data_s2_plt = y_data_s2.reshape(n_airspeed, n_discangle)

print(y_data_interp_plt.shape)
print(airspeed_mat_i[:, :, 0].shape)
print(discangle_mat_i[:, :, 0].shape)


(132, 131)
(132, 131)
(132, 131)


And now we can plot the interpolated data (as a surface)

In [104]:
fig = go.Figure(
    data=[
        go.Surface(
            z=y_data_interp_plt, y=airspeed_mat_i[:, :, 0], x=discangle_mat_i[:, :, 0]
        ),
        go.Scatter3d(
            x=plot_trend_df.discangle,
            y=plot_trend_df.airspeed,
            z=plot_trend_df.load,
            mode="markers",
            marker=dict(color="black", size=4),
        ),
    ]
)

fig.update_layout(
    title=f"Interp at prop speed = {plot_rpm} RPM",
    autosize=False,
    width=500,
    height=500,
    margin=dict(l=65, r=50, b=65, t=90),
)

fig.show()


**From the point of view of fitting, this is a very simple example.**

We have a wonderfully smooth funciton, gridded data (we could even find good resukts with 'ndinterp' or similar), and there is zero noise. In reality we will likely seem some zones which require some smoothing, either due to noise in measurements, or solvers struggling with challenging cases. We will now add some noise into the data. We choose to do this at high axial advance ratios when the flow is going up through the disc.

**Let's generate the noisy, low-fidelity data and build a Kriging mode**

Firstly we shall not treat the Kriger for any noise (note that looking at the lowest prop speed likely gives us the toughest cases)

In [105]:
lf_noise_krg_sm = KRG(theta0=[1e-2], eval_noise=False)
lf_noise_df = dummy_prop_example.add_noise_adv_rat(lf_data_df, 0.11)
lf_noise_x_data = prep_data(lf_noise_df, ["discangle", "airspeed", "propspeed"])
lf_noise_y_data = prep_data(lf_noise_df, ["load_noise"])
lf_noise_krg_sm.set_training_values(lf_noise_x_data, lf_noise_y_data)
lf_noise_krg_sm.train()


___________________________________________________________________________
   
                                  Kriging
___________________________________________________________________________
   
 Problem size
   
      # training points.        : 648
   
___________________________________________________________________________
   
 Training
   
   Training ...
   Training - done. Time (sec): 26.1566930


then interpolate and reshape as before:

In [106]:
noise_y_data_interp = lf_noise_krg_sm.predict_values(x_data_interp)
noise_variance = lf_noise_krg_sm.predict_variances(x_data_interp)

noise_y_data_interp_plt = noise_y_data_interp.reshape(n_airspeed, n_discangle)
noise_variance_plt = noise_variance.reshape(n_airspeed, n_discangle)

___________________________________________________________________________
   
 Evaluation
   
      # eval points. : 17292
   
   Predicting ...
   Predicting - done. Time (sec):  2.9948158
   
   Prediction time/pt. (sec) :  0.0001732
   


**Now we can look at the noisy data:**

In [107]:
noise_plot_trend_df = lf_noise_df[lf_noise_df.propspeed == plot_rpm]
fig = go.Figure(
    data=[
        go.Surface(
            z=noise_y_data_interp_plt,
            y=airspeed_mat_i[:, :, 0],
            x=discangle_mat_i[:, :, 0],
            showscale=False,
        ),
        go.Scatter3d(
            x=noise_plot_trend_df.discangle,
            y=noise_plot_trend_df.airspeed,
            z=noise_plot_trend_df.load_noise,
            mode="markers",
            marker=dict(color="black", size=4),
            name="noisy data,"
        ),
        go.Scatter3d(
            x=noise_plot_trend_df.discangle,
            y=noise_plot_trend_df.airspeed,
            z=noise_plot_trend_df.load,
            mode="markers",
            marker=dict(color="red", size=4),
            name="true data (not used in the fit)",
        ),
    ]
)

fig.update_layout(
    title=f"Interp at prop speed = {plot_rpm} RPM",
    autosize=False,
    width=800,
    height=500,
    margin=dict(l=65, r=50, b=65, t=90),
)

fig.show()


**Adding this noise in has done bad things to the fit! Let's try and handle this.**

Let's rebuild the model, evaluating the noise:

In [110]:
lf_noise_krg_sm = KRG(theta0=[1e-2], eval_noise=True)
lf_noise_df = dummy_prop_example.add_noise_adv_rat(lf_data_df, 0.11)
lf_noise_x_data = prep_data(lf_noise_df, ["discangle", "airspeed", "propspeed"])
lf_noise_y_data = prep_data(lf_noise_df, ["load_noise"])
lf_noise_krg_sm.set_training_values(lf_noise_x_data, lf_noise_y_data)
lf_noise_krg_sm.train()

___________________________________________________________________________
   
                                  Kriging
___________________________________________________________________________
   
 Problem size
   
      # training points.        : 648
   
___________________________________________________________________________
   
 Training
   
   Training ...
   Training - done. Time (sec): 30.6155794


In [108]:
noise_y_data_interp = lf_noise_krg_sm.predict_values(x_data_interp)
noise_variance = lf_noise_krg_sm.predict_variances(x_data_interp)

noise_y_data_interp_plt = noise_y_data_interp.reshape(n_airspeed, n_discangle)
noise_variance_plt = noise_variance.reshape(n_airspeed, n_discangle)

___________________________________________________________________________
   
 Evaluation
   
      # eval points. : 17292
   
   Predicting ...
   Predicting - done. Time (sec):  2.7705472
   
   Prediction time/pt. (sec) :  0.0001602
   


In [109]:
noise_plot_trend_df = lf_noise_df[lf_noise_df.propspeed == plot_rpm]
fig = go.Figure(
    data=[
        go.Surface(
            z=noise_y_data_interp_plt,
            y=airspeed_mat_i[:, :, 0],
            x=discangle_mat_i[:, :, 0],
            showscale=False,
        ),
        go.Scatter3d(
            x=noise_plot_trend_df.discangle,
            y=noise_plot_trend_df.airspeed,
            z=noise_plot_trend_df.load_noise,
            mode="markers",
            marker=dict(color="black", size=4),
            name="noisy data,"
        ),
        go.Scatter3d(
            x=noise_plot_trend_df.discangle,
            y=noise_plot_trend_df.airspeed,
            z=noise_plot_trend_df.load,
            mode="markers",
            marker=dict(color="red", size=4),
            name="true data (not used in the fit)",
        ),
    ]
)

fig.update_layout(
    title=f"Interp at prop speed = {plot_rpm} RPM",
    autosize=False,
    width=800,
    height=500,
    margin=dict(l=65, r=50, b=65, t=90),
)

fig.show()


This is has done a remarkably well at getting rid of the random noise we put it at challenging axial advance ratios. We could look at some real metrics, perhaps I will come back to this.

# Now let's consider some high-fidelity data

We will build a full factorial dataset, at each datapoint we had low-fidelity data at. However we won't use this in the fitting, instead we will *just* use it for plotting purposes.

In [121]:
ff_hf_data_df: pd.DataFrame = dummy_prop_example.hf_data(
    lf_independent[:, 0],
    lf_independent[:, 1],
    lf_independent[:, 2],
    1000.0,
    2700.0,
)

display(ff_hf_data_df)

airspeed  discangle    propspeed          load
0         0.0      -90.0   300.000000    230.850000
1         0.0      -90.0   442.857143    503.054082
2         0.0      -90.0   585.714286    879.952041
3         0.0      -90.0   728.571429   1361.543878
4         0.0      -90.0   871.428571   1947.829592
..        ...        ...          ...           ...
643      60.0       90.0   728.571429  10488.834353
644      60.0       90.0   871.428571  12293.857209
645      60.0       90.0  1014.285714  14144.788606
646      60.0       90.0  1157.142857  16052.242640
647      60.0       90.0  1300.000000  18023.850000

[648 rows x 4 columns]

We will now compare the two datasets:

In [122]:
rpms = np.unique(lf_data_df.propspeed.to_numpy())
rpm = plot_rpm
lf_plot_trend_df = lf_data_df[lf_data_df.propspeed == rpm]
hf_plot_trend_df = ff_hf_data_df[ff_hf_data_df.propspeed == rpm]

fig = go.Figure(
    data=[
        go.Scatter3d(
            x=noise_plot_trend_df.discangle,
            y=noise_plot_trend_df.airspeed,
            z=noise_plot_trend_df.load_noise,
            mode="markers",
            marker=dict(color="black", size=4),
            name="low fidelity",
        ),
        go.Scatter3d(
            x=hf_plot_trend_df.discangle,
            y=hf_plot_trend_df.airspeed,
            z=hf_plot_trend_df.load,
            mode="markers",
            marker=dict(color="blue", size=4),
            name="high fidelity",
        ),
    ]
)

fig.update_layout(
    scene=dict(
        xaxis_title="disc angle [deg]",
        yaxis_title="airspeed [m/s]",
        zaxis_title="thrust [N]",
    ),
    title=f"Prop speed is {rpm} RPM",
)


**Now lets generate a Latin-Hypercube Sample of the data, with far fewer points**

This will not be used for a standalone Kriging surrogate, instead it will feed into the co-Kriging surrogate.

We will use the same limits as before.

In [123]:
hf_lhs = LHS(xlimits=xlimits)
number_of_lf_samples = 40
lhs_hf_independent = hf_lhs(number_of_lf_samples)

Now let us calculate the data at each LHS point, note that we won't add noise to the HF data, we assume this data is of higher quality. We can add noise if we like though, it will still be handled.


In [124]:
lhs_hf_data_df: pd.DataFrame = dummy_prop_example.hf_data(
    lhs_hf_independent[:, 0],
    lhs_hf_independent[:, 1],
    lhs_hf_independent[:, 2],
    1000.0,
    2700.0,
)

display(lhs_hf_data_df)

airspeed  discangle  propspeed          load
0      12.75     -78.75      612.5   -701.380357
1      48.75      33.75      937.5   7108.382098
2       6.75     -65.25     1137.5   2061.018364
3      57.75     -47.25      837.5  -5224.066157
4       3.75     -51.75     1187.5   2994.284717
5      30.75     -69.75     1162.5  -2544.228598
6      17.25     -87.75      362.5  -1251.398020
7      56.25      47.25      337.5   3912.983310
8       9.75      65.25      912.5   3692.901367
9       0.75      69.75      737.5   1501.727895
10     29.25      83.25      587.5   4638.647096
11     41.25     -60.75      712.5  -4020.684250
12      2.25     -15.75     1012.5   2514.010674
13     35.25      51.75     1037.5   8086.979225
14      5.25      60.75      812.5   2435.985157
15     38.25     -42.75     1112.5  -2070.936480
16     24.75      42.75      312.5   1645.949291
17     26.25       2.25      862.5   2082.345992
18      8.25      29.25      787.5   2230.151180
19     54.75      74.25     1237.5  15397.741909
20     51.75      11.25      987.5   4377.683584
21     21.75     -29.25      487.5   -595.500423
22     33.75      -2.25      387.5    257.207523
23     14.25       6.75      512.5    870.403073
24     44.25      78.75      537.5   6010.397853
25     15.75     -33.75      887.5    511.153012
26     11.25      -6.75     1062.5   2636.963831
27     32.25     -38.25      687.5  -1667.569476
28     18.75      24.75      662.5   2229.105064
29     39.75     -83.25      412.5  -3545.705179
30     23.25      87.75      462.5   3087.720367
31     47.25      38.25     1287.5  10798.048284
32     42.75     -24.75      437.5  -1390.468935
33     50.25     -20.25      562.5  -1368.385448
34     36.75      15.75      762.5   3038.359278
35     59.25      56.25      637.5   7782.682671
36     20.25     -11.25     1262.5   3216.346608
37     45.75     -74.25     1087.5  -5721.913118
38     27.75     -56.25     1212.5  -1180.036034
39     53.25      20.25      962.5   5740.792274

**We can now begin to cosider co-kriging, where we can use the high fidelity data to improve the low-fidelity model**

Let's sort the training data (again in the case of the noisy lf data)

In [125]:
lf_noise_x_data = prep_data(lf_noise_df, ["discangle", "airspeed", "propspeed"])
lf_noise_y_data = prep_data(lf_noise_df, ["load_noise"])

hf_x_data = prep_data(lhs_hf_data_df, ["discangle", "airspeed", "propspeed"])
hf_y_data = prep_data(lhs_hf_data_df, ["load"])

**Now we can make the Multi-Fidelity Kriging (MFK) model**

In [126]:
sm = MFK(theta0=[1e-2], eval_noise=True)
# low-fidelity dataset names being integers from 0 to level-1
sm.set_training_values(lf_noise_x_data, lf_noise_y_data, name=0)
# high-fidelity dataset without name
sm.set_training_values(hf_x_data, hf_y_data)
# train the model
sm.train()

___________________________________________________________________________
   
                                    MFK
___________________________________________________________________________
   
 Problem size
   
      # training points.        : 40
   
___________________________________________________________________________
   
 Training
   
   Training ...
   Training - done. Time (sec): 25.5021744


**For the interpolation, we use the same condtions as we looked at previously for the low-fidelity data**

In [127]:
mfk_vec_interp = sm.predict_values(x_data_interp)
mfk_mat_plt = mfk_vec_interp.reshape(n_airspeed, n_discangle)

___________________________________________________________________________
   
 Evaluation
   
      # eval points. : 17292
   
   Predicting ...
   Predicting - done. Time (sec):  2.6216650
   
   Prediction time/pt. (sec) :  0.0001516
   


**Now we can plot the data found from the co-Kriging model**

In [128]:

fig = go.Figure(
    data=[
        go.Surface(
            z=mfk_mat_plt,
            y=airspeed_mat_i[:, :, 0],
            x=discangle_mat_i[:, :, 0],
            showscale=False,
        ),
        go.Scatter3d(
            x=noise_plot_trend_df.discangle,
            y=noise_plot_trend_df.airspeed,
            z=noise_plot_trend_df.load_noise,
            mode="markers",
            marker=dict(color="black", size=4),
            name="noisy data (used for LF model)",
        ),
        go.Scatter3d(
            x=noise_plot_trend_df.discangle,
            y=noise_plot_trend_df.airspeed,
            z=noise_plot_trend_df.load,
            mode="markers",
            marker=dict(color="red", size=4),
            name="non-noisy LF data (not used)",
        ),
        go.Scatter3d(
            x=hf_plot_trend_df.discangle,
            y=hf_plot_trend_df.airspeed,
            z=hf_plot_trend_df.load,
            mode="markers",
            marker=dict(color="blue", size=4),
            name="FF high fidelity (not used (only LHS))",
        ),
    ]
)

fig.update_layout(
    title=f"Interp at prop speed = {plot_rpm} RPM",
    autosize=False,
    width=800,
    height=500,
    margin=dict(l=65, r=50, b=65, t=90),
)

fig.show()


This seems like witchcraft! Lets now check 1300 RPM, to see how it did here:

In [129]:
rpm = 1300.0
x_data_interp[:,2] = rpm
mfk_vec_interp = sm.predict_values(x_data_interp)
mfk_mat_plt = mfk_vec_interp.reshape(n_airspeed, n_discangle)
noise_plot_trend_df = lf_noise_df[lf_noise_df.propspeed == rpm]
hf_plot_trend_df = ff_hf_data_df[ff_hf_data_df.propspeed == rpm]

___________________________________________________________________________
   
 Evaluation
   
      # eval points. : 17292
   
   Predicting ...
   Predicting - done. Time (sec):  4.2592473
   
   Prediction time/pt. (sec) :  0.0002463
   


In [130]:

fig = go.Figure(
    data=[
        go.Surface(
            z=mfk_mat_plt,
            y=airspeed_mat_i[:, :, 0],
            x=discangle_mat_i[:, :, 0],
            showscale=False,
        ),
        go.Scatter3d(
            x=noise_plot_trend_df.discangle,
            y=noise_plot_trend_df.airspeed,
            z=noise_plot_trend_df.load_noise,
            mode="markers",
            marker=dict(color="black", size=4),
            name="noisy data (used for LF model)",
        ),
        go.Scatter3d(
            x=noise_plot_trend_df.discangle,
            y=noise_plot_trend_df.airspeed,
            z=noise_plot_trend_df.load,
            mode="markers",
            marker=dict(color="red", size=4),
            name="non-noisy LF data (not used)",
        ),
        go.Scatter3d(
            x=hf_plot_trend_df.discangle,
            y=hf_plot_trend_df.airspeed,
            z=hf_plot_trend_df.load,
            mode="markers",
            marker=dict(color="blue", size=4),
            name="FF high fidelity (not used (only LHS))",
        ),
    ]
)

fig.update_layout(
    title=f"Interp at prop speed = {rpm} RPM",
    autosize=False,
    width=800,
    height=500,
    margin=dict(l=65, r=50, b=65, t=90),
)

fig.show()


A key thing to remember is that we didn't have access to the blue markers in the above plots, they are just the true high-fidelity function evalution and the corresponsing low-fidelity points. We used just 40 HF function evaluations. I also tried 10 and it wasn't so good. It seems like ~30 starts to get you ball park.

# MAGIC